In [1]:
import numpy as np
import time
from memory_profiler import memory_usage

np.random.seed(42)

def transpose(matrix):
    return [list(row) for row in zip(*matrix)]

def matmul(A, B):
    result = []
    for i in range(len(A)):
        row = []
        for j in range(len(B[0])):
            row.append(sum(A[i][k] * B[k][j] for k in range(len(A[0]))))
        result.append(row)
    return result

def identity_matrix(n):
    return [[1 if i == j else 0 for j in range(n)] for i in range(n)]

def diagonal_inv(sigma, tol=1e-10):
    return [[1/sigma[i] if i == j and sigma[i] > tol else 0 for j in range(len(sigma))] for i in range(len(sigma))]

def norm(v):
    return sum(x**2 for x in v) ** 0.5

def dot(u, v):
    return sum(u[i]*v[i] for i in range(len(u)))

def subtract(u, v):
    return [u[i] - v[i] for i in range(len(u))]

def scalar_multiply(s, v):
    return [s * x for x in v]

def gram_schmidt(A):
    Q = []
    for a in A:
        u = a[:]
        for q in Q:
            proj = scalar_multiply(dot(u, q), q)
            u = subtract(u, proj)
        u_norm = norm(u)
        if u_norm > 1e-10:
            Q.append(scalar_multiply(1/u_norm, u))
    return Q

def eigen_decomposition_sym(A, num_iter=100):
    n = len(A)
    V = identity_matrix(n)
    for _ in range(num_iter):
        for p in range(n):
            for q in range(p+1, n):
                if abs(A[p][q]) < 1e-10:
                    continue
                theta = 0.5 * np.arctan2(2*A[p][q], A[q][q] - A[p][p])
                cos = np.cos(theta)
                sin = np.sin(theta)
                for i in range(n):
                    Api = A[i][p]
                    Aiq = A[i][q]
                    A[i][p] = cos * Api - sin * Aiq
                    A[i][q] = sin * Api + cos * Aiq
                for j in range(n):
                    Apj = A[p][j]
                    Aqj = A[q][j]
                    A[p][j] = cos * Apj - sin * Aqj
                    A[q][j] = sin * Apj + cos * Aqj
                for i in range(n):
                    Vip = V[i][p]
                    Viq = V[i][q]
                    V[i][p] = cos * Vip - sin * Viq
                    V[i][q] = sin * Vip + cos * Viq
    eigenvalues = [A[i][i] for i in range(n)]
    return eigenvalues, V

def svd_inverse(A):
    A_T = transpose(A)
    ATA = matmul(A_T, A)
    eigvals, V = eigen_decomposition_sym([row[:] for row in ATA])
    sigma = [eigval**0.5 if eigval > 0 else 0 for eigval in eigvals]
    sigma_inv = diagonal_inv(sigma)
    V_T = transpose(V)
    AV = matmul(A, V)
    U = []
    for i in range(len(AV[0])):
        col = [AV[j][i] for j in range(len(AV))]
        s = sigma[i]
        if s > 1e-10:
            U.append([x / s for x in col])
        else:
            U.append([0.0] * len(AV))
    U_T = transpose(U)
    temp = matmul(V, sigma_inv)
    return matmul(temp, U_T)

def generate_random_matrix(n):
    return np.random.randint(1, 10, (n, n)).tolist()

def compute_error(A, A_inv):
    A_np = np.array(A)
    A_inv_np = np.array(A_inv)
    identity = np.eye(len(A_np))
    return np.linalg.norm(A_np @ A_inv_np - identity)

def wrapper(func, *args):
    return func(*args)

if __name__ == '__main__':
    matrix_sizes = [3, 5, 10, 100, 1000]
    for size in matrix_sizes:
        A = generate_random_matrix(size)
        cond_number = np.linalg.cond(np.array(A))
        start_time = time.time()
        mem_usage, A_inv = memory_usage((wrapper, (svd_inverse, A)), retval=True, max_iterations=1)
        end_time = time.time()
        execution_time = end_time - start_time
        peak_memory = max(mem_usage) - min(mem_usage)
        error = compute_error(A, A_inv)
        print(f"\nSize {size}x{size}")
        print(f"Condition number: {cond_number:.2e}")
        print(f"Execution time: {execution_time:.6f} seconds")
        print(f"Peak memory usage: {peak_memory:.6f} MiB")
        print(f"Error ||AA⁻¹ - I||: {error:.2e}")
        print(f"Inverse matrix {size}x{size}:")
        for row in A_inv:
            formatted_row = [round(float(val), 4) for val in row]
            print(formatted_row)



Size 3x3
Condition number: 1.33e+02
Execution time: 0.734141 seconds
Peak memory usage: 34.953125 MiB
Error ||AA⁻¹ - I||: 2.90e-01
Inverse matrix 3x3:
[-0.9991, -4.5017, 3.4258]
[0.3809, 2.1281, -1.4444]
[0.8077, 2.8652, -2.2886]

Size 5x5
Condition number: 1.33e+02
Execution time: 0.551999 seconds
Peak memory usage: 11.687500 MiB
Error ||AA⁻¹ - I||: 2.10e+00
Inverse matrix 5x5:
[1.5511, -2.2001, 0.9949, -2.534, 2.0694]
[0.3993, -0.3485, 0.1194, -0.3662, 0.3667]
[-0.7258, 1.1905, -0.4361, 1.1486, -1.1183]
[-0.4042, 0.4657, -0.1996, 0.5985, -0.3431]
[-0.2771, 0.1428, -0.216, 0.2639, -0.2009]

Size 10x10
Condition number: 3.87e+02
Execution time: 0.461621 seconds
Peak memory usage: 0.812500 MiB
Error ||AA⁻¹ - I||: 3.71e+00
Inverse matrix 10x10:
[0.376, -0.4601, 0.3665, 0.0146, -0.0853, 0.7346, 0.2251, -0.1466, -0.3765, -0.2276]
[0.9917, -1.3283, 0.876, 0.1041, -0.0907, 2.1881, 0.5154, -0.0416, -1.5909, -1.0814]
[-0.8874, 0.985, -0.7571, 0.0208, 0.047, -1.604, -0.368, 0.0058, 1.1357, 0.8